# jamba-test-sandbox.ipynb


https://hf.co/BEE-spoke-data/Jamba-900M-doc-writer


---


In [ ]:
#@markdown add auto-Colab formatting with `IPython.display`
from IPython.display import HTML, display
# colab formatting
def set_css():
    display(
        HTML(
            """
  <style>
    pre {
        white-space: pre-wrap;
    }
  </style>
  """
        )
    )

get_ipython().events.register("pre_run_cell", set_css)

In [ ]:
model_name = "BEE-spoke-data/Jamba-900M-doc-writer" # @param {type:"string"}
model_name

'BEE-spoke-data/Jamba-900M-doc-writer'

In [ ]:
!nvidia-smi
!free -h

Sun May 19 19:50:00 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  NVIDIA L4                      Off | 00000000:00:03.0 Off |                    0 |
| N/A   47C    P8              12W /  72W |      1MiB / 23034MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

## setup

In [ ]:
!pip install -U -q ninja
!pip install -U -q transformers accelerate datasets
!MAX_JOBS=4 pip install flash-attn -q --no-build-isolation
!pip install -U -q git+https://github.com/state-spaces/mamba.git git+https://github.com/Dao-AILab/causal-conv1d.git

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.2/307.2 kB 5.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.1/9.1 MB 20.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.6/302.6 kB 14.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 542.0/542.0 kB 28.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 401.2/401.2 kB 15.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 10.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 14.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 14.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 12.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.2/43.2 kB 6.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done


In [ ]:
# Use a pipeline as a high-level helper
import torch
from transformers import pipeline
from transformers import AutoTokenizer, AutoModelForCausalLM

print(f"loading:\t{model_name}")
torch.cuda.empty_cache()

tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    torch_dtype=torch.bfloat16,
    attn_implementation="flash_attention_2",
    device_map="auto",
)

pipe = pipeline("text-generation", model=model, tokenizer=tokenizer)

loading:	BEE-spoke-data/Jamba-900M-doc-writer


tokenizer_config.json:   0%|          | 0.00/1.09k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/598k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.75M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/417 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.07k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.78G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/132 [00:00<?, ?B/s]

In [ ]:
pipe.model = torch.compile(pipe.model)

/usr/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


## inference

- the model is trained on long, textbook-like data.
- It wants some direction, so give it an 'introduction' to your book, and it will take it from there




In [ ]:
#@title define prompt

prompt_text = """**Introduction to Automating Meme Creation**

In the digital age, memes have emerged as a universal language of humor, satire, and commentary, resonating across cultures and communities. The art of meme creation, which once involved manual image editing and captioning, is now evolving with the integration of automation technologies. This guide aims to introduce you to the fascinating world of automating meme creation, a process that combines creativity with efficiency.

Automating the creation of memes involves using software tools and algorithms that can generate humorous images and text based on predefined templates or through more dynamic, AI-driven processes. This not only speeds up the meme-making process but also opens up new possibilities for creativity and spontaneity. Whether you're a social media manager looking to engage with a digital audience, a content creator in search of efficiency, or simply a meme enthusiast curious about the potential of automation, this guide will provide you with the essential knowledge and tools to get started.

From understanding the basics of meme formats and popular themes to exploring advanced AI tools that can generate memes based on textual prompts, this guide covers a wide range of topics. We'll delve into the various software and platforms available, discuss the ethical considerations of automated content creation, and offer practical tips on how to create memes that capture the zeitgeist of your audience.

Prepare to harness the power of automation and inject a dose of fun and innovation into your meme-making journey. Let’s dive into the world of automated meme creation and discover how to make your content stand out in the ever-expanding sea of online humor. 🌿✨🚀
"""

prompt_text = """# Introduction to the Design and Architecture of Underwater Cities

## 1.1 Overview

Underwater cities, once the realm of science fiction, are now approaching the fringes of feasibility. As humanity seeks innovative solutions to urban overpopulation, climate change, and resource scarcity, the ocean offers an intriguing frontier for expansion. This chapter introduces the fundamental concepts and challenges involved in the design and architecture of underwater cities, setting the stage for a deeper exploration of the technical, environmental, and societal considerations that underpin this ambitious endeavor.

## 1.2 Historical Context and Inspiration

The concept of underwater living has fascinated humanity for centuries. From the myth of Atlantis to Jules Verne's "20,000 Leagues Under the Sea," the allure of life beneath the waves has been a powerful motif in literature and popular culture. More recently, video games like *Bioshock* have envisioned detailed, albeit dystopian, underwater cities that captivate the imagination.

However, the real-world inspiration for underwater habitats often stems from scientific endeavors. Projects such as the Aquarius Reef Base and the International Space Station have provided valuable insights into living in isolated and extreme environments, offering lessons that are directly applicable to underwater urbanization.

## 1.3 The Promise and Potential of Underwater Cities

The development of underwater cities promises numerous benefits:

- **Space Optimization:** Earth's surface is becoming increasingly crowded. Expanding downward into the ocean provides a novel way to alleviate land scarcity.
- **Environmental Stewardship:** By creating sustainable underwater habitats, we can minimize human impact on terrestrial ecosystems and promote ocean conservation.
- **Economic Opportunities:** Underwater cities could foster new industries, including marine biotechnology, aquaculture, and underwater tourism.
- **Climate Resilience:** Submerged habitats offer protection from natural disasters such as hurricanes and floods, which are exacerbated by climate change.

## 1.4 Key Challenges

Designing and constructing underwater cities entails overcoming significant challenges:

- **Structural Integrity:** Ensuring that buildings can withstand immense water pressure, corrosion, and potential seismic activity is paramount.
- **Sustainable Energy:** Developing reliable and sustainable energy sources to power underwater habitats is crucial, considering the isolation from traditional power grids.
- **Life Support Systems:** Maintaining breathable air, clean water, and food supply chains in an underwater environment requires sophisticated technology and logistics.
- **Psychological Well-being:** Addressing the mental health and social needs of residents living in a confined and isolated environment is essential for long-term habitation.

## 1.5 Technical Foundations

The successful design and architecture of underwater cities rely on a multidisciplinary approach, incorporating advances in marine engineering, materials science, environmental science, and urban planning. This section will explore the technical foundations required to bring the vision of underwater cities to life:

- **Marine Engineering:** This field focuses on the design, construction, and maintenance of structures in marine environments. It includes the study of hydrodynamics, buoyancy, and underwater construction techniques.
- **Materials Science:** Developing materials that can withstand harsh underwater conditions, resist corrosion, and provide insulation is critical. Innovations in composites, polymers, and coatings play a significant role.
- **Environmental Science:** Understanding the ocean's ecosystem is vital for minimizing ecological impact and ensuring sustainable coexistence. This involves studying marine biology, oceanography, and environmental impact assessment.
- **Urban Planning and Architecture:** Designing functional, livable spaces that promote community and well-being is essential. This includes considerations of spatial layout, lighting, and aesthetics.

## 1.6 Case Studies and Precedents

This textbook will examine a range of case studies and precedents, both real and fictional, to provide context and inspiration. These include:

- **Aquarius Reef Base:** The world's only undersea research laboratory, located in the Florida Keys.
- **Poseidon Undersea Resort:** A proposed luxury underwater hotel in Fiji.
- **Bioshock's Rapture:** A detailed, albeit fictional, depiction of an underwater city that offers valuable design and architectural insights.
- **SeaOrbiter:** A conceptual floating oceanographic laboratory designed by French architect Jacques Rougerie.

## 1.7 Conclusion

The exploration of underwater city design and architecture is a journey into the unknown, blending cutting-edge technology with bold vision. As we embark on this journey, this textbook aims to provide a comprehensive guide, drawing from diverse fields and real-world examples to equip future architects, engineers, and planners with the knowledge and inspiration needed to transform the dream of underwater living into reality.

In the following chapters, we will delve deeper into the specific technical, environmental, and societal aspects of underwater city design, beginning with an in-depth look at marine engineering and the unique challenges posed by the ocean environment."""


print(prompt_text)

# Introduction to the Design and Architecture of Underwater Cities

## 1.1 Overview

Underwater cities, once the realm of science fiction, are now approaching the fringes of feasibility. As humanity seeks innovative solutions to urban overpopulation, climate change, and resource scarcity, the ocean offers an intriguing frontier for expansion. This chapter introduces the fundamental concepts and challenges involved in the design and architecture of underwater cities, setting the stage for a deeper exploration of the technical, environmental, and societal considerations that underpin this ambitious endeavor.

## 1.2 Historical Context and Inspiration

The concept of underwater living has fascinated humanity for centuries. From the myth of Atlantis to Jules Verne's "20,000 Leagues Under the Sea," the allure of life beneath the waves has been a powerful motif in literature and popular culture. More recently, video games like *Bioshock* have envisioned detailed, albeit dystopian, underwater

In [ ]:
%%time

torch.cuda.empty_cache()
result = pipe(
    prompt_text,
    max_new_tokens=12288,
    do_sample=True,
    temperature=0.8,
    top_p=0.95,
    eta_cutoff=0.0006,
    repetition_penalty=1.2,
    no_repeat_ngram_size=5,
)[0]
generated_text = result['generated_text'].replace(prompt_text, "")
print(generated_text)

 We will also discuss how these issues emerge, then review current debates within the landscape, exploring some key questions:

- __1
2 Concepts about the Ocean Management Approach

# 1
3 Artificial Surface Structures (EMS)

# 2
4 Emerging Technologies Across the World

# 3
5 Trends in Atmospheric Chemistry

# 4
6 Expanded Environmentally Controllable Landscapes

# 5 Natural Disasters and Greenhouses

# 6 Chapter 2: Sustainability

# 7
6.1 Explanation and Impact

As you read through this book, many questions arise regarding the nature and significance of artificial surfaces, not just the physical characteristics they contain, but also the various factors influencing their appearance and interactions. For instance, if water moves between two planes at different rates, the interaction may increase or decrease exponentially; therefore, what causes a difference? How might environmental changes affect your perception of what appears to be different, or at least different, things than those 

In [ ]:
import hashlib
from pathlib import Path
#@markdown save to file
def compute_sha256(input_string, num_chars:int = 12):
    # Encode the input string to bytes
    byte_string = input_string.encode('utf-8')

    # Create a sha256 hash object
    sha256_hash = hashlib.sha256()

    # Update the hash object with the byte string
    sha256_hash.update(byte_string)

    # Return the hexadecimal representation of the hash (last n chars)
    return sha256_hash.hexdigest()[-num_chars:]

out_dir = Path.cwd() / 'generated'
out_dir.mkdir(exist_ok=True)
out_file = out_dir / f'{compute_sha256(prompt_text)}.txt'
print(out_file.name)
with open(out_file, 'w', encoding='utf-8', errors='ignore') as f:
    f.write(generated_text)

01201d526637.txt


In [ ]:
num_tokens = len(pipe.tokenizer.encode(generated_text, padding=False, truncation=False))
print(f"Number of tokens: {num_tokens}")
result['generated_text']

Number of tokens: 12276


'# Introduction to the Design and Architecture of Underwater Cities\n\n## 1.1 Overview\n\nUnderwater cities, once the realm of science fiction, are now approaching the fringes of feasibility. As humanity seeks innovative solutions to urban overpopulation, climate change, and resource scarcity, the ocean offers an intriguing frontier for expansion. This chapter introduces the fundamental concepts and challenges involved in the design and architecture of underwater cities, setting the stage for a deeper exploration of the technical, environmental, and societal considerations that underpin this ambitious endeavor.\n\n## 1.2 Historical Context and Inspiration\n\nThe concept of underwater living has fascinated humanity for centuries. From the myth of Atlantis to Jules Verne\'s "20,000 Leagues Under the Sea," the allure of life beneath the waves has been a powerful motif in literature and popular culture. More recently, video games like *Bioshock* have envisioned detailed, albeit dystopian, 